In [ ]:
# open h5ad in R?

In [2]:
library(dplyr)
library(Seurat)
library(anndata)
library(ggplot2)

In [16]:
# datasets
tab0 = read.delim('cellxgene_datasets.txt', sep = '\t')
tab0[1:2,]

dataset_id                          
1 0895c838-e550-48a3-a777-dbcd35d30272
2 00ff600e-6e2e-4d76-846f-0eec4f0ae417
  collection_name                                                                                                                  
1 Single-Cell, Single-Nucleus, and Spatial RNA Sequencing of the Human Liver Identifies Cholangiocyte and Mesenchymal Heterogeneity
2 Single-cell analysis of human B cell maturation predicts how antibody class switching shapes selection dynamics                  
  dataset_title                        soma_joinid
1 Healthy human liver: B cells         0          
2 Human tonsil nonlymphoid cells scRNA 1

In [3]:
ad <- read_h5ad("neurog2_ascl1_neurog1_census.h5ad")
ad

AnnData object with n_obs × n_vars = 3792093 × 3
    obs: 'dataset_id', 'assay', 'cell_type', 'tissue', 'tissue_general', 'suspension_type', 'disease'
    var: 'soma_joinid', 'feature_id', 'feature_name', 'feature_length', 'nnz', 'n_measured_obs'

In [4]:
exp_mat = t(ad$X)
rownames(exp_mat) = c('Neurog2', 'Ascl1', 'Neurog1')

In [5]:
mtd = ad$obs
head(mtd)

dataset_id                           assay     cell_type             
0 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
1 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
2 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
3 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
4 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
5 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
  tissue       tissue_general suspension_type disease
0 diencephalon brain          cell            normal 
1 diencephalon brain          cell            normal 
2 diencephalon brain          cell            normal 
3 diencephalon brain          cell            normal 
4 diencephalon brain          cell            normal 
5 diencephalon brain          cell            normal

In [6]:
# cpm-normalize the raw counts
seu = CreateSeuratObject(counts = exp_mat, meta.data = mtd)
seu <- NormalizeData(seu, normalization.method = "RC", scale.factor = 1e6)
exp1 = LayerData(seu, assay = 'RNA', layer = 'data') # cpm

Warning message:
“Data is of class dgRMatrix. Coercing to dgCMatrix.”
Normalizing layer: counts



In [7]:
sum(exp1['Neurog2',]>0)
sum(exp1['Ascl1',]>0)
sum(exp1['Neurog1',]>0)

[1] 208584

[1] 53397

[1] 3847

In [8]:
gene1_exp = exp1['Neurog2',]
gene2_exp = exp1['Ascl1',]

vec1 = rank(gene1_exp)
vec2 = rank(gene2_exp)

vec1 <- vec1/max(vec1, na.rm = T)
vec2 <- vec2/max(vec2, na.rm = T)

In [9]:
cor(vec1, vec2, method = 'spearman')

[1] 0.02511608

In [10]:
id1 = which(vec1>0.7 & vec2>0.7) # dbl-positive
id2 = which(vec1>0.7 & vec2<0.7) # neurog2
id3 = which(vec1<0.7 & vec2>0.7) # ascl1

length(id1)
length(id2)
length(id3)

[1] 5878

[1] 202706

[1] 47519

In [11]:
mtd[id1[1:10],]

dataset_id                           assay     cell_type             
1   6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
2   6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
56  6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
97  6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
112 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
158 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
180 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
189 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 GABAergic neuron      
190 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
212 6de332e1-465e-4243-9412-6fdc7497e99d 10x 3' v3 neural progenitor cell
    tissue       tissue_general suspension_type disease
1   diencephalon brain          cell            normal 
2   diencephalon brain          cell            normal 
56  diencephalon brain          cell            normal 
97  diencephalon brain          cell            normal 
112 diencephalon brain          cell            normal 
158 diencephalon brain          cell            normal 
180 diencephalon brain          cell            normal 
189 diencephalon brain          cell            normal 
190 diencephalon brain          cell            normal 
212 diencephalon brain          cell            normal

In [23]:
# cluster 8,10,16,22 for dbl-pos; cluster 32 for neurog2+
mtd[id1,] %>% group_by(cell_type) %>% reframe(count = n()) %>% arrange(-count)

cell_type                                                                          
1  glutamatergic neuron                                                               
2  neural progenitor cell                                                             
3  GABAergic neuron                                                                   
4  neuron                                                                             
5  L4/5 intratelencephalic projecting glutamatergic neuron of the primary motor cortex
6  L2/3-6 intratelencephalic projecting glutamatergic neuron                          
7  neuroblast (sensu Vertebrata)                                                      
8  glioblast                                                                          
9  oligodendrocyte precursor cell                                                     
10 macroglial cell                                                                    
11 pyramidal neuron                                                                   
12 L6 intratelencephalic projecting glutamatergic neuron of the primary motor cortex  
13 hypendymal cell                                                                    
14 blood vessel endothelial cell                                                      
15 erythrocyte                                                                        
16 L5/6 near-projecting glutamatergic neuron of the primary motor cortex              
17 vascular leptomeningeal cell                                                       
18 unknown                                                                            
19 ependymal cell                                                                     
20 astrocyte                                                                          
21 L6 corticothalamic-projecting glutamatergic cortical neuron                        
22 corticothalamic-projecting glutamatergic cortical neuron                           
23 neural stem cell                                                                   
24 L5 extratelencephalic projecting glutamatergic cortical neuron                     
25 inhibitory interneuron                                                             
26 microglial cell                                                                    
27 oligodendrocyte                                                                    
28 L2/3 intratelencephalic projecting glutamatergic neuron of the primary motor cortex
29 Purkinje cell                                                                      
30 hippocampal neuron                                                                 
31 sncg GABAergic cortical interneuron                                                
32 sst GABAergic cortical interneuron                                                 
33 cerebellar granule cell                                                            
34 interneuron                                                                        
35 noradrenergic cell                                                                 
36 pituitary gland cell                                                               
   count
1  2115 
2  1404 
3   737 
4   419 
5   360 
6   290 
7   150 
8   148 
9    45 
10   36 
11   17 
12   16 
13   16 
14   14 
15   14 
16   12 
17   11 
18   10 
19    9 
20    7 
21    6 
22    6 
23    6 
24    5 
25    4 
26    4 
27    3 
28    2 
29    2 
30    2 
31    2 
32    2 
33    1 
34    1 
35    1 
36    1

In [15]:
length(unique(as.character(mtd$dataset_id)))
length(unique(as.character(mtd$dataset_id[id1])))

[1] 33

[1] 24

In [26]:
tab1 = tab0[match(unique(as.character(mtd$dataset_id[id1])), tab0$dataset_id),]
tab1

dataset_id                          
46  6de332e1-465e-4243-9412-6fdc7497e99d
124 76b604f3-bb29-4db7-be2b-6500dc5fbdb7
145 a14a995b-2f1d-40df-8f61-ab2754cac630
184 899e2906-cdb1-4dcc-8dd8-3e3fead6c910
188 8d8411b2-eb8c-4d8b-9cf1-c605de44d1e6
228 f71f046d-ea2d-4470-ac38-572cbb06ee12
241 66ff82b4-9380-469c-bc4b-cfa08eacd325
377 72eb2332-b308-4014-8d25-95233a9aff1e
403 d622cee4-56e1-44ba-8b05-fd2f0f2032e6
537 50d79de5-bd17-4d14-a295-199d71ff56be
602 cb5efdb0-f91c-4cbd-9ad4-9d4fa41c572d
635 28c696bb-9549-434b-9340-dc745a846f9a
679 812fa7bd-db15-4357-b2c9-efc8e1eb0450
688 5e765f97-1cf1-407e-a86c-e28701f4749d
690 e0ed3c55-aff6-4bb7-b6ff-98a2d90b890c
696 c88e2a9c-72b8-4a88-a2f6-e428eada0c86
701 3bbb6cf9-72b9-41be-b568-656de6eb18b5
705 98e5ea9f-16d6-47ec-a529-686e76515e39
717 a9affc92-a291-4eb9-996f-147392132323
718 79a2344d-eddd-45b1-b376-39eddfab1899
747 dbb4e1ed-d820-4e83-981f-88ef7eb55a35
769 f16a8f4d-bc97-43c5-a2f6-bbda952e4c5c
780 35081d47-99bf-4507-9541-735428df9a9f
789 d7291f04-fbbb-4d65-990a-f01fa44e915b
    collection_name                                                                                                   
46  Developmental trajectories of thalamic nuclei revealed by single-cell transcriptome profiling and Shh perturbation
124 Developmental trajectories of thalamic nuclei revealed by single-cell transcriptome profiling and Shh perturbation
145 Developmental trajectories of thalamic nuclei revealed by single-cell transcriptome profiling and Shh perturbation
184 Developmental trajectories of thalamic nuclei revealed by single-cell transcriptome profiling and Shh perturbation
188 Developmental trajectories of thalamic nuclei revealed by single-cell transcriptome profiling and Shh perturbation
228 Developmental trajectories of thalamic nuclei revealed by single-cell transcriptome profiling and Shh perturbation
241 Tabula Muris Senis                                                                                                
377 Cellular development and evolution of the mammalian cerebellum                                                    
403 An integrated transcriptomic and epigenomic atlas of mouse primary motor cortex cell types                        
537 An integrated transcriptomic and epigenomic atlas of mouse primary motor cortex cell types                        
602 Phenotypic variation of transcriptomic cell types in mouse motor cortex                                           
635 Shared and distinct transcriptomic cell types across neocortical areas                                            
679 A taxonomy of transcriptomic cell types across the isocortex and hippocampal formation                            
688 An integrated transcriptomic and epigenomic atlas of mouse primary motor cortex cell types                        
690 A transcriptomic atlas of the mouse cerebellum reveals regional specializations and novel cell types              
696 An integrated transcriptomic and epigenomic atlas of mouse primary motor cortex cell types                        
701 Molecular and spatial signatures of mouse brain aging at single-cell resolution                                   
705 Tabula Muris Senis                                                                                                
717 An integrated transcriptomic and epigenomic atlas of mouse primary motor cortex cell types                        
718 Developmental trajectories of thalamic nuclei revealed by single-cell transcriptome profiling and Shh perturbation
747 HypoMap – a unified single cell gene expression atlas of the murine hypothalamus                                  
769 Tabula Muris Senis                                                                                                
780 An integrated transcriptomic and epigenomic atlas of mouse primary motor cortex cell types                        
789 A taxonomy of transcriptomic cell types across the isocortex and hippocampal formation                            
    

In [27]:
length(unique(tab1$collection_name))

[1] 10

In [24]:
# Alex's target genes
alex = c('Bcl11a', 'Bcl11b', 'Nhlh1', 'Nhlh2', 'Sox2', 'Sox9', 'Gfap',
        'Pax6', 'Prom1', 'Foxj1', 'Rbfox3', 'Nes', 'Hopx', 'Dcx',
        'Bdnf', 'Pdgfra', 'S100b')
length(alex)

[1] 17

In [25]:
# other coexpressing genes
currgene = 'Pax6'
sum(exp1[currgene,]>0)

# no. of cells with >0 exp in each case
sum(exp1[currgene, id1]>0)
sum(exp1[currgene, id2]>0)
sum(exp1[currgene, id3]>0)

exp_vec = exp1[currgene,]
vec3 = rank(exp_vec)
vec3 <- vec3/max(vec3, na.rm = T)
plotdf = data.frame(gene = currgene, 
                    ctype = c(rep('double+', length(id1)), rep('Neurog2+', length(id2)), rep('Ascl1+', length(id3))),
                    exp = c(log2(1+exp_vec[id1]), log2(1+exp_vec[id2]), log2(1+exp_vec[id3])),
                    rank_exp = c(vec3[id1], vec3[id2], vec3[id3]))
plotdf$ctype = factor(plotdf$ctype, levels = c('double+', 'Neurog2+', 'Ascl1+'))

ERROR: Error in .subscript.2ary(x, i, , drop = TRUE): subscript out of bounds
